### 加载
#### 加载模型

In [1]:
from unsloth import FastModel
import torch
from client import ClientSender
import uuid
import zmq
import msgpack

# 实例化网络传输对象
client = ClientSender(server_address="121.196.205.73", port=5678)

max_seq_length = 2048 # 模型的最大序列长度，默认是1024
lora_rank = 32 # LoRA的秩，越大越好，但会消耗更多内存 #8

model, tokenizer = FastModel.from_pretrained(
    model_name = "./models/Qwen3-8B",
    max_seq_length = max_seq_length, # 可以选择任意长度以支持长上下文！
    load_in_4bit = False,  # 4位量化以减少内存使用
    load_in_8bit = True, # 精度更高，但使用2倍内存
    full_finetuning = False, # 完全微调
)

🦥 Unsloth: Will patch your computer to enable 2x faster free finetuning.
🦥 Unsloth Zoo will now patch everything to make training faster!
INFO 05-04 01:33:32 [__init__.py:239] Automatically detected platform cuda.
==((====))==  Unsloth 2025.4.7: Fast Qwen3 patching. Transformers: 4.51.3. vLLM: 0.8.4.
   \\   /|    NVIDIA vGPU-32GB. Num GPUs = 1. Max memory: 31.484 GB. Platform: Linux.
O^O/ \_/ \    Torch: 2.6.0+cu124. CUDA: 8.9. CUDA Toolkit: 12.4. Triton: 3.2.0
\        /    Bfloat16 = TRUE. FA [Xformers = 0.0.29.post2. FA2 = False]
 "-____-"     Free license: http://github.com/unslothai/unsloth
Unsloth: Fast downloading is enabled - ignore downloading bars which are red colored!


Loading checkpoint shards:   0%|          | 0/5 [00:00<?, ?it/s]

#### 加载 Lora 设置

In [2]:
model = FastModel.get_peft_model(
    model,
    finetune_vision_layers     = False, # 仅处理文本层或者模型没有视觉层时关闭
    finetune_language_layers   = True,  # 应该保持开启！
    finetune_attention_modules = True,  # 注意力机制对GRPO有好处
    finetune_mlp_modules       = True,  # 应该始终保持开启！

    r = lora_rank,           # 更大 = 更高的精度，但可能过拟合
    lora_alpha = lora_rank,  # 建议alpha至少等于r
    lora_dropout = 0,
    use_gradient_checkpointing = "unsloth",
    bias = "none",
    random_state = 3407, # 使用同一个随机数种子
)

Unsloth: Making `model.base_model.model.model` require gradients


#### 加载、构造数据集

##### 构造系统提示词

In [2]:
# 设置系统提示此
reasoning_start = "<think>"
reasoning_end   = "</think>"
solution_start = "<code>"
solution_end   = "</code>"

system_prompt = \
f"""你是一个 Blender 的材质生成器，你将会考虑问题并提供材质对应的 python 代码，该代码应该可以且仅在 Blender 中创建对应材质，你生成出的python代码应当就是最终结果，用户可以直接使用，不需要用户更改，你也不会使用任何外部文件。
请将思考过程放在 {reasoning_start} 和 {reasoning_end} 之间。
然后，请在 {solution_start} 和 {solution_end} 之间提供你的答案。"""
system_prompt

'你是一个 Blender 的材质生成器，你将会考虑问题并提供材质对应的 python 代码，该代码应该可以且仅在 Blender 中创建对应材质，你生成出的python代码应当就是最终结果，用户可以直接使用，不需要用户更改，你也不会使用任何外部文件。\n请将思考过程放在 <think> 和 </think> 之间。\n然后，请在 <code> 和 </code> 之间提供你的答案。'

##### 构造数据集

In [6]:
from datasets import Dataset
import random
import uuid

dataset = []

level3 = [
    "椅子上的纹路：这款材质的纹理呈现出精致的花纹，可能是圆形、对称或者不规则的图案，表面看起来既舒适又具有视觉冲击力。椅子上的纹理材质常常是通过精细的织物或者皮革等材质呈现，给使用者带来视觉上的享受与舒适的触感。设计师往往会利用这些纹路来增强座椅的美感与舒适度，特别适用于豪华沙发和高端办公椅。",
    "椅子上的纹路：这款材质的纹理呈现出精致的花纹，可能是圆形、对称或者不规则的图案，表面看起来既舒适又具有视觉冲击力。椅子上的纹理材质常常是通过精细的织物或者皮革等材质呈现，给使用者带来视觉上的享受与舒适的触感。设计师往往会利用这些纹路来增强座椅的美感与舒适度，特别适用于豪华沙发和高端办公椅。",
    "椅子上的纹路：这款材质的纹理呈现出精致的花纹，可能是圆形、对称或者不规则的图案，表面看起来既舒适又具有视觉冲击力。椅子上的纹理材质常常是通过精细的织物或者皮革等材质呈现，给使用者带来视觉上的享受与舒适的触感。设计师往往会利用这些纹路来增强座椅的美感与舒适度，特别适用于豪华沙发和高端办公椅。",
    "椅子上的纹路：这款材质的纹理呈现出精致的花纹，可能是圆形、对称或者不规则的图案，表面看起来既舒适又具有视觉冲击力。椅子上的纹理材质常常是通过精细的织物或者皮革等材质呈现，给使用者带来视觉上的享受与舒适的触感。设计师往往会利用这些纹路来增强座椅的美感与舒适度，特别适用于豪华沙发和高端办公椅。",
    "椅子上的纹路：这款材质的纹理呈现出精致的花纹，可能是圆形、对称或者不规则的图案，表面看起来既舒适又具有视觉冲击力。椅子上的纹理材质常常是通过精细的织物或者皮革等材质呈现，给使用者带来视觉上的享受与舒适的触感。设计师往往会利用这些纹路来增强座椅的美感与舒适度，特别适用于豪华沙发和高端办公椅。",
    "椅子上的纹路：这款材质的纹理呈现出精致的花纹，可能是圆形、对称或者不规则的图案，表面看起来既舒适又具有视觉冲击力。椅子上的纹理材质常常是通过精细的织物或者皮革等材质呈现，给使用者带来视觉上的享受与舒适的触感。设计师往往会利用这些纹路来增强座椅的美感与舒适度，特别适用于豪华沙发和高端办公椅。",
    "椅子上的纹路：这款材质的纹理呈现出精致的花纹，可能是圆形、对称或者不规则的图案，表面看起来既舒适又具有视觉冲击力。椅子上的纹理材质常常是通过精细的织物或者皮革等材质呈现，给使用者带来视觉上的享受与舒适的触感。设计师往往会利用这些纹路来增强座椅的美感与舒适度，特别适用于豪华沙发和高端办公椅。",
    "椅子上的纹路：这款材质的纹理呈现出精致的花纹，可能是圆形、对称或者不规则的图案，表面看起来既舒适又具有视觉冲击力。椅子上的纹理材质常常是通过精细的织物或者皮革等材质呈现，给使用者带来视觉上的享受与舒适的触感。设计师往往会利用这些纹路来增强座椅的美感与舒适度，特别适用于豪华沙发和高端办公椅。",
    "椅子上的纹路：这款材质的纹理呈现出精致的花纹，可能是圆形、对称或者不规则的图案，表面看起来既舒适又具有视觉冲击力。椅子上的纹理材质常常是通过精细的织物或者皮革等材质呈现，给使用者带来视觉上的享受与舒适的触感。设计师往往会利用这些纹路来增强座椅的美感与舒适度，特别适用于豪华沙发和高端办公椅。",
    "椅子上的纹路：这款材质的纹理呈现出精致的花纹，可能是圆形、对称或者不规则的图案，表面看起来既舒适又具有视觉冲击力。椅子上的纹理材质常常是通过精细的织物或者皮革等材质呈现，给使用者带来视觉上的享受与舒适的触感。设计师往往会利用这些纹路来增强座椅的美感与舒适度，特别适用于豪华沙发和高端办公椅。",
    "椅子上的纹路：这款材质的纹理呈现出精致的花纹，可能是圆形、对称或者不规则的图案，表面看起来既舒适又具有视觉冲击力。椅子上的纹理材质常常是通过精细的织物或者皮革等材质呈现，给使用者带来视觉上的享受与舒适的触感。设计师往往会利用这些纹路来增强座椅的美感与舒适度，特别适用于豪华沙发和高端办公椅。",
    "椅子上的纹路：这款材质的纹理呈现出精致的花纹，可能是圆形、对称或者不规则的图案，表面看起来既舒适又具有视觉冲击力。椅子上的纹理材质常常是通过精细的织物或者皮革等材质呈现，给使用者带来视觉上的享受与舒适的触感。设计师往往会利用这些纹路来增强座椅的美感与舒适度，特别适用于豪华沙发和高端办公椅。",
    "椅子上的纹路：这款材质的纹理呈现出精致的花纹，可能是圆形、对称或者不规则的图案，表面看起来既舒适又具有视觉冲击力。椅子上的纹理材质常常是通过精细的织物或者皮革等材质呈现，给使用者带来视觉上的享受与舒适的触感。设计师往往会利用这些纹路来增强座椅的美感与舒适度，特别适用于豪华沙发和高端办公椅。",
]

# 任务前缀列表
user_start = ["做这个材质:", "帮我生成这个：", "这个问题需要你的帮助, 帮我生成", "我希望你能帮助我生成", "请帮我做一个材质", "希望你帮我生成", "请你为我做一个", "你能做一下这个吗?", "", "请完成以下任务:", "帮我搞一个材质:", "能否帮我生成", "请协助我生成一个"]

# 构造数据集
for task in level3:
    user_prompts = user_start + user_start + user_start + user_start + user_start + user_start
    for user in user_prompts:
        dataset.append({
            "prompt": [
                {"role": "system", "content": system_prompt},
                {"role": "user", "content": user + task},
            ],
            "taskid": uuid.uuid4().hex,
            "goal": task,
        })
    
# 输出最终数据集
final_dataset = Dataset.from_list(dataset)

def print_dataset_length(ds):
    print(f"最终数据集长度: {len(ds)}")

print_dataset_length(final_dataset)

最终数据集长度: 1014


### 定义奖励函数
#### 定义标准格式形式

In [5]:
import re

# 定义正则表达式，用来判断模型的输出是否符合格式要求
match_format = re.compile(
    rf"^[\s]{{0,}}"\
    rf"<think>.+?</think>.*?"\
    rf"<code>(.+?)</code>"\
    rf"[\s]{{0,}}$",
    flags = re.MULTILINE | re.DOTALL
)

match_format.search(
    "<think>Let me think!</think>"\
    "<code>2</code>",
)

<re.Match object; span=(0, 42), match='<think>Let me think!</think><code>2</code>'>

#### 构造奖励函数

In [6]:
# 严格格式判断函数
def match_format_exactly(completions, **kwargs):
    """格式判断函数，严格判断格式是否匹配
    """
    scores = []
    for completion in completions:
        score = 0
        response = completion[0]["content"]
        # Match if format is seen exactly!
        if match_format.search(response) is not None: score += 3.0
        scores.append(score)
    return scores

In [7]:
# 弱格式判断函数
def match_format_approximately(prompts, completions, **kwargs):
    """弱格式判断奖励，即使没有严格对应，也可以根据使用的标签数量来做出相应的奖励
    """
    question = prompts[0][-1]["content"]
    responses = [completion[0]["content"] for completion in completions]
        
    print('*'*20, f"Question:\n{question}", f"\nResponse:\n{responses[0]}")
    
    scores = []
    for completion in completions:
        score = 0
        response = completion[0]["content"]
        # 数一数看到多少个关键词——如果太多，我们会惩罚你！
        # 如果我们看到1个关键词，那么加一些积分！如果更多了，那么就应当扣除一些分
        score += 0.5 if response.count(reasoning_start) == 1 else -0.5
        score += 0.5 if response.count(reasoning_end)   == 1 else -0.5
        score += 0.5 if response.count(solution_start)  == 1 else -0.5
        score += 0.5 if response.count(solution_end)    == 1 else -0.5
        scores.append(score)
    return scores

In [8]:
# 获取代码
def code_extractor(code):
    match = re.search(r'<code>(.*?)</code>', code, flags=re.DOTALL)
    if not match:
        return ""
    content = match.group(1).strip()
    if not content:
        return ""
    return content

In [9]:
# 生成的图像和描述的相似度
def accuracy_reward(goal, taskid, completions, prompts, **kwargs):
    """计算生成的图像和描述的相似度
    """
    
    WEIGHT = 2 # 用来在归一化之后加权
    scores = []
    names = []
    
    # 构造传输对象
    materials = {
        "head": {
            "input": goal[0],
            "taskid": taskid[0],
            "request": []
        },
        "outputs": []
    }
    
    # 填充材质代码
    for completion in completions:
        response = completion[0]["content"]
        code = code_extractor(response)
        print("AR_CODE________________")
        print(type(code))
        print(code)
        
        name = f"M{len(materials['outputs'])+1}"
        names.append(name)
        
        materials["outputs"].append({
            "name": name,
            "code": code
        })
    
    print("AR_MT________________")
    print(type(materials))
    print(materials)

    # 添加分数
    c =  client.send_materials(materials)
    print("AR_P________________")
    print(type(c))
    print(c)
    results = c.get("accuracy_rank", {})

    
    for name in names:
        score = int(results.get(name, 0))
        scores.append(score)
    
    # 归一化并加权
    min_s, max_s = min(scores), max(scores)
    if max_s > min_s:
        scores[:] = [(s - min_s) / (max_s - min_s) for s in scores]
        # 对分数加权
        scores = [s * WEIGHT for s in scores]
    else:
        scores = [0,0,0,0]
    
    # 返回分数
    print("accuracy_reward" + str(results))
    return scores

In [10]:
# 图像是否有意义
def meaning_reward(goal, taskid, completions, **kwargs):
    """计算生成的图像是否有意义
    """
    
    WEIGHT = 1 # 用来在归一化之后加权
    scores = []
    names = []
    
    # 构造传输对象
    materials = {
        "head": {
            "input": goal[0],
            "taskid": taskid[0],
            "request": []
        },
        "outputs": []
    }
    
    # 填充材质代码
    for completion in completions:
        response = completion[0]["content"]
        code = code_extractor(response)
        print("MR_CODE________________")
        print(type(code))
        print(code)
        
        name = f"M{len(materials['outputs'])+1}"
        names.append(name)
        
        materials["outputs"].append({
            "name": name,
            "code": code
        })

    print("MR_MT________________")
    print(type(materials))
    print(materials)
    
    # 添加分数
    c =  client.send_materials(materials)
    print("MR_P________________")
    print(type(c))
    print(c)
    results = c.get("meaning_rank", {})
    
    for name in names:
        score = int(results.get(name, 0))
        scores.append(score)
    
    # 归一化并加权
    min_s, max_s = min(scores), max(scores)
    if max_s > min_s:
        scores[:] = [(s - min_s) / (max_s - min_s) for s in scores]
        scores[:] = [s * WEIGHT for s in scores]
    else:
        scores = [0,0,0,0]
    
    # 返回分数
    print("meaning_reward" + str(results))
    return scores

In [11]:
# 代码是否报错
def error_check(goal, taskid, completions, **kwargs):
    """检查生成的代码是否报错
    """
    
    WEIGHT = 2
    scores = []
    names = []
    
    # 构造传输对象
    materials = {
        "head": {
            "input": goal[0],
            "taskid": taskid[0],
            "request": []
        },
        "outputs": []
    }
    
    # 填充材质代码
    for completion in completions:
        response = completion[0]["content"]
        code = code_extractor(response)
        print("EC_CODE________________")
        print(type(code))
        print(code)
        
        name = f"M{len(materials['outputs'])+1}"
        names.append(name)
        
        materials["outputs"].append({
            "name": name,
            "code": code
        })

    print("EC_MT________________")
    print(type(materials))
    print(materials)
    
    # 添加分数
    c =  client.send_materials(materials)
    print("EC_P________________")
    print(type(c))
    print(c)
    results = c.get("status", {})
    # results = client.send_materials(materials).get("status", {})
    
    for name in names:
        score = results.get(name, False)
        scores.append(WEIGHT if score else 0)
    
    # 检查是否存在梯度，如果没有梯度了就放弃
    min_s, max_s = min(scores), max(scores)
    if not max_s > min_s:
        scores = [0,0,0,0]
    
    # 返回分数
    print("error_check" + str(results))
    return scores

### 训练部分
#### 训练配置

In [ ]:
max_prompt_length = 256

# 使用 GRPO 训练器，并构造训练器
from trl import GRPOConfig, GRPOTrainer
training_args = GRPOConfig(
    beta = 0.001, # 设置为 0 以禁用 KL 散度惩罚 # defaults to 0.04
    learning_rate = 5e-6,
    adam_beta1 = 0.9,
    adam_beta2 = 0.99,
    weight_decay = 0.1,
    warmup_ratio = 0.1,
    lr_scheduler_type = "cosine",
    optim = "adamw_torch_fused",
    logging_steps = 1,
    per_device_train_batch_size = 4,
    gradient_accumulation_steps = 1, # 增加到4，以便更顺滑地训练 #1
    num_generations = 4, # Decrease if out of memory
    max_prompt_length = max_prompt_length,
    max_completion_length = max_seq_length - max_prompt_length,
    # num_train_epochs = 1, # Set to 1 for a full training run
    max_steps = 1200, # 训练步数
    save_steps = 200, # 每200步保存一次
    max_grad_norm = 0.1,
    report_to = "none", # Can use Weights & Biases
    output_dir = "outputs_ArtI_12b_bf4_qlora", # 输出目录
    
    
)

#### 开始训练

In [13]:
# 创建训练器，并且使用上面给出的 reward function
trainer = GRPOTrainer(
    model = model,
    processing_class = tokenizer,
    reward_funcs = [
        # 格式奖励
        match_format_exactly,
        match_format_approximately,
        
        # 图像意义奖励
        accuracy_reward,
        meaning_reward,
        
        # 运行错误检查
        error_check,
        
    ],
    args = training_args,
    train_dataset = final_dataset,
)
trainer.train()

==((====))==  Unsloth - 2x faster free finetuning | Num GPUs used = 1
   \\   /|    Num examples = 2,366 | Num Epochs = 1 | Total steps = 1,200
O^O/ \_/ \    Batch size per device = 4 | Gradient accumulation steps = 1
\        /    Data Parallel GPUs = 1 | Total batch size (4 x 1 x 1) = 4
 "-____-"     Trainable parameters = 43,646,976/8,234,382,336 (0.53% trained)
`generation_config` default values have been modified to match model-specific defaults: {'max_length': 40960, 'top_k': 20, 'top_p': 0.95, 'bos_token_id': 151643, 'eos_token_id': [151645, 151643]}. If this is not desired, please set these values explicitly.
`use_cache=True` is incompatible with gradient checkpointing. Setting `use_cache=False`.


******************** Question:
请帮我做一个材质透明的材质 
Response:
<think>
好的，用户让我帮他做一个透明材质。首先，我得回想一下在Blender中如何创建透明材质。透明材质通常需要使用到原理化材质节点，比如Principled BSDF节点，然后调整透明度参数。

用户可能是在做某种需要透明效果的物体，比如玻璃、水或者半透明的物体。不过用户没有具体说明用途，所以得保持通用。透明材质通常需要开启透明度通道，可能还需要调整折射率或者光泽度，但用户只提到透明，所以可能不需要太复杂的设置。

接下来，我需要考虑Blender的版本。不同版本的节点系统可能略有不同，但一般来说，Principled BSDF节点是通用的。用户可能使用的是较新的版本，所以用Principled BSDF比较合适。不过，有时候用户可能想要更简单的节点设置，比如直接使用透明度节点，但Principled BSDF更灵活，适合大多数情况。

然后，我需要确定是否需要使用混合节点。比如，可能需要将透明度与基础颜色结合，或者使用法线贴图等。但用户只是要透明材质，可能不需要额外的节点。所以，最简单的做法是使用Principled BSDF节点，设置透明度为1，同时确保材质输出节点正确连接。

另外，用户可能没有提到是否需要反射或折射，但透明材质通常需要这些效果。比如，玻璃材质需要折射和反射，所以可能需要调整Principled BSDF的折射率和粗糙度参数。不过用户可能只是想要一个简单的透明效果，比如完全透明，所以可能需要将透明度设为1，并关闭其他不必要的属性。

还要注意材质的输出节点是否正确。在Blender中，材质输出节点的表面属性需要连接到Principled BSDF的BSDF输出。另外，确保透明度通道是开启的，可能需要检查材质的设置是否正确。

最后，生成Python代码的时候，需要正确使用bpy模块来创建材质和节点。需要确保节点的链接正确，参数设置正确。比如，创建Principled BSDF节点，设置透明度为1，然后连接到材质输出。可能还需要检查节点的名称是否正确，避免重复。

总结一下，用户需要的是一个简单的透明材质，使用Principled BSDF节点，设置透明度为1，连接到材质输出。可能还需要调整其他参数，但用户没有特别说明，所以保

Unsloth: Will smartly offload gradients to save VRAM!
******************** Question:
请协助我生成一个蓝色的金属材质：它呈现出深邃的蓝色，金属反射效果明显，适合用在精密机械或未来感十足的设计中。 
Response:
<think>
好的，用户想要生成一个蓝色的金属材质，深邃且有明显的金属反射，适合精密机械或未来感设计。首先，我需要考虑在Blender中如何实现这种效果。通常金属材质会使用Principled BSDF节点，因为它能很好地模拟材质的各个属性。

首先，确定颜色。深邃的蓝色可以用一个RGB节点或者直接使用颜色值。可能需要较暗的蓝色，比如#003366或者更暗一些，比如#002244，这样看起来更深邃。不过用户可能想要更具体的色调，可能需要调整色值，但用户没有给出具体数值，所以选择一个常见的深蓝作为基础。

接下来是金属度。金属材质需要高金属度，所以Principled BSDF的Metallic值应该设为1。粗糙度（Roughness）要低，这样反射更清晰，但可能需要稍微调整，让表面有一定的细节，比如0.2到0.3之间，这样既有光泽又不完全镜面，更真实。

反射部分，使用光泽度较高的材质，可能需要调整Specular值，不过Principled节点的Specular属性在较新的Blender版本中已经整合到Metallic里，所以可能不需要单独调整。但为了更强烈的反射，可以增加Specular值，或者使用一个高光节点。不过可能直接通过调整Metallic和Roughness就能达到效果。

另外，可能需要添加一些环境反射，使用World节点或者HDRI环境，但用户可能只需要材质本身，所以不需要考虑环境部分。不过材质的反射效果会受到环境的影响，所以可能需要建议使用适当的环境设置，但用户可能只需要材质节点，所以暂时不考虑。

然后，考虑是否需要添加法线贴图或粗糙度贴图来增加细节，但用户没有提到，所以可能保持基础材质。如果用户需要更复杂的细节，可能需要额外的节点，但根据问题描述，用户可能只需要基础的蓝色金属材质。

可能需要使用一个Color节点来设置基色，连接到Principled BSDF的Base Color输入。然后调整Metallic和Roughness参数。此外，

AttributeError: 'list' object has no attribute 'get'

In [ ]:
import matplotlib.pyplot as plt
import pandas as pd
import numpy as np
import re
import os
from collections import defaultdict
import seaborn as sns

# 设置Seaborn样式以获得更好看的图表
sns.set_style("whitegrid")
plt.rcParams['figure.figsize'] = (12, 8)
plt.rcParams['font.size'] = 12

def extract_rewards_from_log(log_path):
    """从训练日志文件中提取奖励数据
    
    参数:
        log_path: 日志文件路径
        
    返回:
        包含步骤和对应奖励的pandas DataFrame
    """
    # 存储数据的字典
    data = defaultdict(list)
    step_pattern = re.compile(r'Step\s+(\d+)')
    reward_pattern = re.compile(r'Reward_(\d+):\s+([-\d.]+)')
    mean_reward_pattern = re.compile(r'Mean Reward:\s+([-\d.]+)')
    
    if not os.path.exists(log_path):
        print(f"日志文件 {log_path} 不存在!")
        return pd.DataFrame()
    
    with open(log_path, 'r') as f:
        for line in f:
            # 提取步骤
            step_match = step_pattern.search(line)
            if step_match:
                current_step = int(step_match.group(1))
                data['step'].append(current_step)
                
                # 提取各个奖励函数的值
                rewards = reward_pattern.findall(line)
                for idx, value in rewards:
                    data[f'reward_{idx}'].append(float(value))
                
                # 提取平均奖励
                mean_match = mean_reward_pattern.search(line)
                if mean_match:
                    data['mean_reward'].append(float(mean_match.group(1)))
    
    return pd.DataFrame(data)

def extract_rewards_from_trainer(trainer):
    """从trainer对象中直接提取奖励数据
    
    参数:
        trainer: GRPOTrainer对象
        
    返回:
        包含步骤和对应奖励的pandas DataFrame
    """
    if hasattr(trainer, 'state') and hasattr(trainer.state, 'log_history'):
        data = defaultdict(list)
        for entry in trainer.state.log_history:
            if 'step' in entry:
                data['step'].append(entry['step'])
                
                # 提取各个奖励
                for key, value in entry.items():
                    if key.startswith('reward_'):
                        data[key].append(value)
                
                # 提取平均奖励
                if 'mean_reward' in entry:
                    data['mean_reward'].append(entry['mean_reward'])
                
        return pd.DataFrame(data)
    else:
        print("训练器没有日志历史或者结构不符合预期!")
        return pd.DataFrame()

def plot_rewards(data, title="GRPO训练奖励曲线", save_path=None, moving_avg_window=5):
    """绘制奖励折线图
    
    参数:
        data: 包含奖励数据的DataFrame
        title: 图表标题
        save_path: 保存图表的路径，如果为None则显示图表
        moving_avg_window: 移动平均窗口大小
    """
    if data.empty:
        print("没有数据可以绘图!")
        return
    
    fig, ax = plt.subplots()
    
    # 定义一组专业的颜色
    colors = sns.color_palette('viridis', n_colors=len(data.columns)-1)
    
    # 绘制每个奖励函数的曲线
    for i, col in enumerate([col for col in data.columns if col != 'step']):
        # 原始数据点（透明度降低）
        ax.plot(data['step'], data[col], alpha=0.3, color=colors[i], label=f"{col} (raw)")
        
        # 添加移动平均线
        if len(data) >= moving_avg_window:
            moving_avg = data[col].rolling(window=moving_avg_window).mean()
            ax.plot(data['step'], moving_avg, linewidth=2, color=colors[i], label=f"{col} ({moving_avg_window}-point avg)")
    
    # 添加标题和标签
    ax.set_title(title, fontsize=16, fontweight='bold')
    ax.set_xlabel('Training Steps', fontsize=14)
    ax.set_ylabel('Reward', fontsize=14)
    
    # 添加网格线和图例
    ax.grid(True, linestyle='--', alpha=0.7)
    ax.legend(loc='best', fontsize=12)
    
    # 添加统计信息
    if 'mean_reward' in data.columns:
        final_mean = data['mean_reward'].iloc[-1]
        max_mean = data['mean_reward'].max()
        min_mean = data['mean_reward'].min()
        stats_text = f"Final mean reward: {final_mean:.4f}\nMax mean reward: {max_mean:.4f}\nMin mean reward: {min_mean:.4f}"
        plt.figtext(0.02, 0.02, stats_text, fontsize=12, bbox=dict(facecolor='white', alpha=0.8))
    
    plt.tight_layout()
    
    # 保存或显示图表
    if save_path:
        plt.savefig(save_path, dpi=300, bbox_inches='tight')
        print(f"图表已保存到 {save_path}")
    else:
        plt.show()

# 示例用法
def visualize_rewards(trainer=None, log_file=None, output_path=None):
    """可视化训练奖励
    
    参数:
        trainer: GRPOTrainer对象，如果提供则直接从训练器中提取数据
        log_file: 日志文件路径，如果trainer不可用则从日志文件中提取数据
        output_path: 图表保存路径，默认为当前目录下的'reward_plot.png'
    """
    if output_path is None:
        output_path = 'reward_plot.png'
    
    if trainer is not None:
        data = extract_rewards_from_trainer(trainer)
    elif log_file is not None:
        data = extract_rewards_from_log(log_file)
    else:
        print("请提供trainer对象或日志文件路径!")
        return
    
    plot_rewards(data, save_path=output_path)
    
    # 输出一些统计信息
    if not data.empty and 'mean_reward' in data.columns:
        print("\n--- 奖励统计信息 ---")
        print(f"最终平均奖励: {data['mean_reward'].iloc[-1]:.4f}")
        print(f"最大平均奖励: {data['mean_reward'].max():.4f}")
        print(f"最小平均奖励: {data['mean_reward'].min():.4f}")
        
        # 计算奖励增长率
        if len(data) > 1:
            first_reward = data['mean_reward'].iloc[0]
            last_reward = data['mean_reward'].iloc[-1]
            growth = ((last_reward - first_reward) / abs(first_reward)) * 100 if first_reward != 0 else float('inf')
            print(f"奖励增长率: {growth:.2f}%")

# 用法示例
# 1. 使用训练器对象
# visualize_rewards(trainer=trainer)

# 2. 或者使用日志文件
# visualize_rewards(log_file="./outputs_gemma-3_grpo_lora/opt_gemm3_2.log")

# 从训练后直接可视化
# 在训练后调用以下代码即可直接可视化
visualize_rewards(trainer=trainer, output_path="reward_trends.png")

### 模型测试
#### 默认模型测试

In [ ]:
messages = [
    # {"role": "system", "content": "你是一个 GLSL Shader 生成器，你生成出来的应当就是最终结果，可以直接使用，你也不会使用任何外部文件，纯粹程序化生成"},
    # {"role": "system", "content": "你是一个 blender 节点解释器，会和我解释 blender 节点是干什么用的"},
    {"role": "system", "content": "你是一个 Blender 的材质生成器，会直接生成材质对应的 Python 代码，该代码应该可以且仅在 Blender 中创建对应材质，你生成出来的应当就是最终结果，用户可以直接使用，不需要用户更改，你也不会使用任何外部文件"},
    {"role": "user",   "content": "给我生成一个的灰色渐变到黄色的材质"},
]

text = tokenizer.apply_chat_template(
    messages,
    add_generation_prompt = True, # Must add for generation
    tokenize = False,
)
from transformers import TextStreamer
_ = model.generate(
    **tokenizer(text, return_tensors = "pt").to("cuda"),
    max_new_tokens = 1024*2, # Increase for longer outputs!
    # Recommended Gemma-3 settings!
    temperature = 1.0, top_p = 0.95, top_k = 64,
    streamer = TextStreamer(tokenizer, skip_prompt = True),
)

In [ ]:
# 加载原始模型（不包含微调）
from unsloth import FastModel
import torch

# 定义相同的参数
max_seq_length = 1024

# 重新加载原始模型（不应用LoRA权重）
original_model, original_tokenizer = FastModel.from_pretrained(
    model_name = "./models/gemma-3-1b-it",  # 使用原始模型路径
    max_seq_length = max_seq_length,
    load_in_4bit = False,
    load_in_8bit = False,
)

# 测试问题
test_messages = [
    {"role": "system", "content": system_prompt},  # 使用之前定义的系统提示词
    {"role": "user", "content": "What is the sqrt of 101?"},  # 使用同样的测试问题以便比较
]

# 准备输入
test_text = original_tokenizer.apply_chat_template(
    test_messages,
    add_generation_prompt = True,
    tokenize = False,
)

# 使用TextStreamer直接查看输出
from transformers import TextStreamer
print("\n原始模型输出：")
_ = original_model.generate(
    **original_tokenizer(test_text, return_tensors = "pt").to("cuda"),
    max_new_tokens = 1024,
    temperature = 0.8,  # 使用与微调模型相同的温度
    top_p = 0.95,
    top_k = 64,
    streamer = TextStreamer(original_tokenizer, skip_prompt = True),
)

#### finetuning 模型测试

In [ ]:
# 保存 Lora
model.save_lora("grpo_saved_lora")

#### 保存 Lora

In [ ]:
model.save_pretrained("gemma-3")  # Local saving
tokenizer.save_pretrained("gemma-3")

In [ ]:
if True: # Change to True to save finetune!
    model.save_pretrained_merged("gemma-3-finetune", tokenizer)

### 保存为完整模型

##### 保存为 bf16 格式

In [ ]:
# Merge to 16bit
if True: model.save_pretrained_merged("model", tokenizer, save_method = "merged_16bit",)
if True: model.push_to_hub_merged("hf/model", tokenizer, save_method = "merged_16bit", token = "")

# Merge to 4bit
if False: model.save_pretrained_merged("model", tokenizer, save_method = "merged_4bit",)
if False: model.push_to_hub_merged("hf/model", tokenizer, save_method = "merged_4bit", token = "")

# Just LoRA adapters
if False: model.save_pretrained_merged("model", tokenizer, save_method = "lora",)
if False: model.push_to_hub_merged("hf/model", tokenizer, save_method = "lora", token = "")

In [ ]:
if False: # Change to True to upload finetune
    model.push_to_hub_merged(
        "HF_ACCOUNT/gemma-3-finetune", tokenizer,
        token = "hf_..."
    )

In [ ]:
# 保存为 GGUF 格式
# if False:
#     model.save_pretrained_gguf(
#         "gemma-3-finetune",
#         quantization_type = "Q8_0", # For now only Q8_0, BF16, F16 supported
#     )

In [ ]:
# if False: # Change to True to upload GGUF
#     model.push_to_hub_gguf(
#         "gemma-3-finetune",
#         quantization_type = "Q8_0", # Only Q8_0, BF16, F16 supported
#         repo_id = "HF_ACCOUNT/gemma-finetune-gguf",
#         token = "hf_...",
#     )